In [1]:
import torch
from IPython.display import Image  # for displaying images
import os 
import random
import numpy as np
import shutil
from sklearn.model_selection import train_test_split
import xml.etree.ElementTree as ET
from xml.dom import minidom
from tqdm import tqdm
from PIL import Image, ImageDraw
import numpy as np
import matplotlib.pyplot as plt

random.seed(108)

## Convert to YOLO format

```
yolo_labels/
├── 0000/
│   ├── 000000.txt
│   ├── 000001.txt
│   └── ...
├── 0001/
│   ├── 000000.txt
│   ├── 000001.txt
│   └── ...
└── 0020/
    ├── 000000.txt
    ├── 000001.txt
    └── ...
```



In [5]:
# Base path to the folders containing KITTI images
base_folder = '/home/clara/Documents/perception/final_project/dataset/data_tracking_image_2/training/image_02'

# Iterate through subfolders from 0000 to 0020
for folder_num in range(21):  # 0000 to 0020
    folder_name = f"{folder_num:04d}"  # Format folder number as 4 digits
    folder_path = os.path.join(base_folder, folder_name)

    if not os.path.isdir(folder_path):
        print(f"Folder {folder_name} does not exist. Skipping.")
        continue

    # Set to store unique sizes for this folder
    unique_sizes = set()

    # Iterate through all images in the subfolder
    for image_file in os.listdir(folder_path):
        if image_file.endswith(('.png', '.jpg')):
            image_path = os.path.join(folder_path, image_file)
            image = cv2.imread(image_path)
            if image is not None:
                height, width, _ = image.shape
                unique_sizes.add((width, height))  # Add size as a tuple (width, height)

    # Print unique sizes for the current folder
    print(f"Folder: {folder_name}")
    for size in unique_sizes:
        print(f"  Width: {size[0]}, Height: {size[1]}")

    # Reset the set for the next folder (automatically happens as the set is recreated per folder)


Folder: 0000
  Width: 1242, Height: 375
Folder: 0001
  Width: 1242, Height: 375
Folder: 0002
  Width: 1242, Height: 375
Folder: 0003
  Width: 1242, Height: 375
Folder: 0004
  Width: 1242, Height: 375
Folder: 0005
  Width: 1242, Height: 375
Folder: 0006
  Width: 1242, Height: 375
Folder: 0007
  Width: 1242, Height: 375
Folder: 0008
  Width: 1242, Height: 375
Folder: 0009
  Width: 1242, Height: 375
Folder: 0010
  Width: 1242, Height: 375
Folder: 0011
  Width: 1242, Height: 375
Folder: 0012
  Width: 1242, Height: 375
Folder: 0013
  Width: 1242, Height: 375
Folder: 0014
  Width: 1224, Height: 370
Folder: 0015
  Width: 1224, Height: 370
Folder: 0016
  Width: 1224, Height: 370
Folder: 0017
  Width: 1224, Height: 370
Folder: 0018
  Width: 1238, Height: 374
Folder: 0019
  Width: 1238, Height: 374
Folder: 0020
  Width: 1241, Height: 376


In [ ]:
import os

def convert_kitti_to_yolo_by_folder_and_frame(kitti_label_dir, yolo_label_dir, class_map, folder_sizes):
    """
    Convert KITTI annotations to YOLO format and organize by folders and frames.

    Args:
        kitti_label_dir (str): Path to KITTI label files.
        yolo_label_dir (str): Path to save YOLO label files organized by folders and frames.
        class_map (dict): Mapping of KITTI class names to YOLO class IDs.
        folder_sizes (dict): Mapping of folder names to (image_width, image_height).
    """
    os.makedirs(yolo_label_dir, exist_ok=True)

    # Process all KITTI label files
    for label_file in os.listdir(kitti_label_dir):
        if not label_file.endswith('.txt'):
            continue

        kitti_path = os.path.join(kitti_label_dir, label_file)

        with open(kitti_path, 'r') as kitti_file:
            for line in kitti_file.readlines():
                elements = line.strip().split()
                frame_number = elements[0]  # First element specifies the frame number
                class_name = elements[2]

                if class_name == "DontCare" or class_name not in class_map:
                    continue

                # Determine the folder and image size
                folder_name = label_file.replace('.txt', '')  # Folder name matches the label file
                if folder_name not in folder_sizes:
                    print(f"Folder {folder_name} not found in folder_sizes. Skipping.")
                    continue

                image_width, image_height = folder_sizes[folder_name]

                # Convert to YOLO format
                class_id = class_map[class_name]
                x_min, y_min, x_max, y_max = map(float, elements[6:10])
                x_center = ((x_min + x_max) / 2) / image_width
                y_center = ((y_min + y_max) / 2) / image_height
                width = (x_max - x_min) / image_width
                height = (y_max - y_min) / image_height

                # Create subfolder for the sequence
                sequence_folder = os.path.join(yolo_label_dir, folder_name)
                os.makedirs(sequence_folder, exist_ok=True)

                # Write to YOLO label file for the frame
                yolo_label_file = os.path.join(sequence_folder, f"{int(frame_number):06d}.txt")
                with open(yolo_label_file, 'a') as yolo_file:
                    yolo_file.write(f"{class_id} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f}\n")


# Parameters
class_map = {
    'Cyclist': 0,
    'Pedestrian': 1,
    'Car': 2,
}

# Folder sizes based on your earlier results
folder_sizes = {
    '0000': (1242, 375),
    '0001': (1242, 375),
    '0002': (1242, 375),
    '0003': (1242, 375),
    '0004': (1242, 375),
    '0005': (1242, 375),
    '0006': (1242, 375),
    '0007': (1242, 375),
    '0008': (1242, 375),
    '0009': (1242, 375),
    '0010': (1242, 375),
    '0011': (1242, 375),
    '0012': (1242, 375),
    '0013': (1242, 375),
    '0014': (1224, 370),
    '0015': (1224, 370),
    '0016': (1224, 370),
    '0017': (1224, 370),
    '0018': (1238, 374),
    '0019': (1238, 374),
    '0020': (1241, 376),
}


kitti_label_dir = '/dtu/blackhole/09/203497/Perception/final_project/dataset/training/kitti_labels/data_tracking_label_2/training/label_02'
yolo_label_dir = '/dtu/blackhole/09/203497/Perception/final_project/dataset/training/yolo_labels'

convert_kitti_to_yolo_by_folder_and_frame(kitti_label_dir, yolo_label_dir, class_map, folder_sizes)




Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not found in folder_sizes. Skipping.
Folder 0010 not foun

In [ ]:
import os

def convert_kitti_to_yolo_single_sequence(kitti_label_dir, yolo_label_dir, class_map, folder_sizes, sequence):
    """
    Convert KITTI annotations to YOLO format for a single sequence.

    Args:
        kitti_label_dir (str): Path to KITTI label files.
        yolo_label_dir (str): Path to save YOLO label files organized by sequence.
        class_map (dict): Mapping of KITTI class names to YOLO class IDs.
        folder_sizes (dict): Mapping of folder names to (image_width, image_height).
        sequence (str): Sequence to process (e.g., '0001').
    """
    os.makedirs(yolo_label_dir, exist_ok=True)

    label_file = f"{sequence}.txt"  # The label file for the specific sequence
    kitti_path = os.path.join(kitti_label_dir, label_file)

    if not os.path.exists(kitti_path):
        print(f"Label file for sequence {sequence} not found.")
        return

    with open(kitti_path, 'r') as kitti_file:
        for line in kitti_file.readlines():
            elements = line.strip().split()
            frame_number = elements[0]  # First element specifies the frame number
            class_name = elements[2]

            if class_name == "DontCare" or class_name not in class_map:
                continue

            # Determine the image size for the sequence
            if sequence not in folder_sizes:
                print(f"Sequence {sequence} not found in folder_sizes. Skipping.")
                continue

            image_width, image_height = folder_sizes[sequence]

            # Convert to YOLO format
            class_id = class_map[class_name]
            x_min, y_min, x_max, y_max = map(float, elements[6:10])
            x_center = ((x_min + x_max) / 2) / image_width
            y_center = ((y_min + y_max) / 2) / image_height
            width = (x_max - x_min) / image_width
            height = (y_max - y_min) / image_height

            # Create subfolder for the sequence
            sequence_folder = os.path.join(yolo_label_dir, sequence)
            os.makedirs(sequence_folder, exist_ok=True)

            # Write to YOLO label file for the frame
            yolo_label_file = os.path.join(sequence_folder, f"{int(frame_number):06d}.txt")
            with open(yolo_label_file, 'a') as yolo_file:
                yolo_file.write(f"{class_id} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f}\n")

# Parameters
class_map = {
    'Cyclist': 0,
    'Pedestrian': 1,
    'Car': 2,
}

folder_sizes = {
    # '0000': (1242, 375),
    '0001': (1242, 375),
    # Add other sequences as needed
}

kitti_label_dir = '/dtu/blackhole/09/203497/Perception/final_project/dataset/training/kitti_labels/data_tracking_label_2/training/label_02'
yolo_label_dir = '/dtu/blackhole/09/203497/Perception/final_project/dataset/training/yolo_labels'

# Process only sequence 0001
convert_kitti_to_yolo_single_sequence(kitti_label_dir, yolo_label_dir, class_map, folder_sizes, sequence='0001')


## Plot the bboxes from yolo labels

In [19]:
import os
import cv2

def plot_yolo_bboxes(image_dir, label_dir, output_dir, class_names):
    """
    Plot YOLO bounding boxes on training images.

    Args:
        image_dir (str): Path to the directory containing training images.
        label_dir (str): Path to the directory containing YOLO label files.
        output_dir (str): Path to save annotated images.
        class_names (list): List of class names corresponding to class IDs.
    """
    os.makedirs(output_dir, exist_ok=True)

    # Iterate through all images
    for image_file in os.listdir(image_dir):
        if not image_file.endswith(('.png', '.jpg')):
            continue

        # Get corresponding label file
        label_file = os.path.join(label_dir, image_file.replace('.jpg', '.txt').replace('.png', '.txt'))
        if not os.path.exists(label_file):
            print(f"Label file {label_file} for {image_file} not found. Skipping.")
            continue

        # Read image
        image_path = os.path.join(image_dir, image_file)
        image = cv2.imread(image_path)
        if image is None:
            print(f"Could not read image {image_file}. Skipping.")
            continue

        # Read YOLO labels
        with open(label_file, 'r') as lf:
            for line in lf.readlines():
                elements = line.strip().split()
                class_id, x_center, y_center, width, height = map(float, elements)

                # Convert normalized YOLO coordinates to pixel coordinates
                img_h, img_w, _ = image.shape
                x_center *= img_w
                y_center *= img_h
                width *= img_w
                height *= img_h

                x_min = int(x_center - width / 2)
                y_min = int(y_center - height / 2)
                x_max = int(x_center + width / 2)
                y_max = int(y_center + height / 2)

                # Draw bounding box
                color = (0, 255, 0)  # Green for bounding boxes
                cv2.rectangle(image, (x_min, y_min), (x_max, y_max), color, 2)

                # Draw label
                label = f"{class_names[int(class_id)]}"
                cv2.putText(image, label, (x_min, y_min - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, color, 2)

        # Save or display annotated image
        output_path = os.path.join(output_dir, image_file)
        cv2.imwrite(output_path, image)
        print(f"Saved annotated image: {output_path}")


# Parameters
image_dir = '/home/clara/Documents/perception/final_project/dataset/data_tracking_image_2/training/image_02/0000'  # Path to training images
label_dir = '/home/clara/Documents/perception/final_project/dataset/yolo_labels/0000'  # Path to YOLO labels
output_dir = '/home/clara/Documents/perception/final_project/dataset/annotated_images'  # Path to save annotated images
class_names = ['Cyclist', 'Pedestrian', 'Car']  # Update as per your class mapping

# Plot bounding boxes
plot_yolo_bboxes(image_dir, label_dir, output_dir, class_names)


Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000130.png
Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000135.png
Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000113.png
Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000037.png
Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000027.png
Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000082.png
Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000036.png
Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000122.png
Saved annotated image: /home/clara/Documents/perception/final_project/dataset/annotated_images/000120.png
Saved annotated image: /home/clara/Documents/p

In [16]:
import os
import cv2

def plot_yolo_bboxes_by_sequence(image_base_dir, label_base_dir, output_base_dir, class_names):
    """
    Plot YOLO bounding boxes on training images for all the sequences at once.

    Args:
        image_base_dir (str): Path to the base directory containing image sequences (0000, 0001, ...).
        label_base_dir (str): Path to the base directory containing YOLO label sequences.
        output_base_dir (str): Path to save annotated images organized by sequence.
        class_names (list): List of class names corresponding to class IDs.
    """
    os.makedirs(output_base_dir, exist_ok=True)

    # Iterate through each sequence (0000, 0001, ..., 0020)
    for sequence in sorted(os.listdir(image_base_dir)):
        sequence_image_dir = os.path.join(image_base_dir, sequence)
        sequence_label_dir = os.path.join(label_base_dir, sequence)
        sequence_output_dir = os.path.join(output_base_dir, sequence)

        if not os.path.isdir(sequence_image_dir) or not os.path.isdir(sequence_label_dir):
            print(f"Sequence {sequence} not found in both image and label directories. Skipping.")
            continue

        os.makedirs(sequence_output_dir, exist_ok=True)

        # Iterate through all images in the sequence
        for image_file in os.listdir(sequence_image_dir):
            if not image_file.endswith(('.png', '.jpg')):
                continue

            # Get corresponding label file
            label_file = os.path.join(sequence_label_dir, image_file.replace('.jpg', '.txt').replace('.png', '.txt'))
            if not os.path.exists(label_file):
                print(f"Label file {label_file} for {image_file} not found. Skipping.")
                continue

            # Read image
            image_path = os.path.join(sequence_image_dir, image_file)
            image = cv2.imread(image_path)
            if image is None:
                print(f"Could not read image {image_file}. Skipping.")
                continue

            # Read YOLO labels
            with open(label_file, 'r') as lf:
                for line in lf.readlines():
                    elements = line.strip().split()
                    class_id, x_center, y_center, width, height = map(float, elements)

                    # Convert normalized YOLO coordinates to pixel coordinates
                    img_h, img_w, _ = image.shape
                    x_center *= img_w
                    y_center *= img_h
                    width *= img_w
                    height *= img_h

                    x_min = int(x_center - width / 2)
                    y_min = int(y_center - height / 2)
                    x_max = int(x_center + width / 2)
                    y_max = int(y_center + height / 2)

                    # Draw bounding box
                    color = (0, 255, 0)  # Green for bounding boxes
                    cv2.rectangle(image, (x_min, y_min), (x_max, y_max), color, 2)

                    # Draw label
                    label = f"{class_names[int(class_id)]}"
                    cv2.putText(image, label, (x_min, y_min - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, color, 2)

            # Save annotated image
            output_path = os.path.join(sequence_output_dir, image_file)
            cv2.imwrite(output_path, image)
            print(f"Saved annotated image: {output_path}")


# Parameters
image_base_dir = '/home/clara/Documents/perception/final_project/dataset/data_tracking_image_2/training/image_02'  # Path to base directory containing image sequences
label_base_dir = '/home/clara/Documents/perception/final_project/dataset/yolo_labels'  # Path to base directory containing YOLO label sequences
output_base_dir = '/home/clara/Documents/perception/final_project/dataset/annotated_images'  # Path to save annotated images
class_names = ['Cyclist', 'Pedestrian', 'Car']  # Update as per your class mapping

# Plot bounding boxes for all sequences
plot_yolo_bboxes_by_sequence(image_base_dir, label_base_dir, output_base_dir, class_names)


PermissionError: [Errno 13] Permission denied: '/home/clara'

## Split into train/val/test sets

```
splits/
├── images/
│   ├── train/
│   │   ├── 0000_frame1.png
│   │   ├── 0000_frame2.png
│   │   └── ...
│   ├── val/
│   │   ├── 0001_frame1.png
│   │   └── ...
│   └── test/
│       ├── 0002_frame1.png
│       └── ...
├── labels/
│   ├── train/
│   │   ├── 0000_frame1.txt
│   │   ├── 0000_frame2.txt
│   │   └── ...
│   ├── val/
│   │   ├── 0001_frame1.txt
│   │   └── ...
│   └── test/
│       ├── 0002_frame1.txt
│       └── ...

```

In [18]:
import os
import shutil
from sklearn.model_selection import train_test_split

def split_dataset(image_base_dir, label_base_dir, output_base_dir, train_ratio=0.8, val_ratio=0.1):
    """
    Splits the dataset into training, validation, and test sets.

    Args:
        image_base_dir (str): Path to the base directory containing image sequences.
        label_base_dir (str): Path to the base directory containing YOLO label sequences.
        output_base_dir (str): Path to save the split dataset.
        train_ratio (float): Proportion of the dataset to use for training.
        val_ratio (float): Proportion of the dataset to use for validation.
    """
    # Create directories for train, val, and test
    splits = ['train', 'val', 'test']
    for split in splits:
        os.makedirs(os.path.join(output_base_dir, 'images', split), exist_ok=True)
        os.makedirs(os.path.join(output_base_dir, 'labels', split), exist_ok=True)

    # Iterate through each sequence
    for sequence in sorted(os.listdir(image_base_dir)):
        if sequence == '0001':  # Skip this specific sequence
            continue
        sequence_image_dir = os.path.join(image_base_dir, sequence)
        sequence_label_dir = os.path.join(label_base_dir, sequence)

        if not os.path.isdir(sequence_image_dir) or not os.path.isdir(sequence_label_dir):
            print(f"Sequence {sequence} not found in both image and label directories. Skipping.")
            continue

        # Get all image files and corresponding label files
        image_files = sorted([f for f in os.listdir(sequence_image_dir) if f.endswith(('.png', '.jpg'))])
        label_files = sorted([f.replace('.png', '.txt').replace('.jpg', '.txt') for f in image_files])

        # Filter images and labels where label files exist
        valid_pairs = [
            (img_file, lbl_file)
            for img_file, lbl_file in zip(image_files, label_files)
            if os.path.exists(os.path.join(sequence_label_dir, lbl_file))
        ]

        if not valid_pairs:
            print(f"No valid label files found for sequence {sequence}. Skipping.")
            continue

        image_files, label_files = zip(*valid_pairs)

        # Split into train, val, and test
        train_images, test_images, train_labels, test_labels = train_test_split(
            image_files, label_files, test_size=1 - train_ratio, random_state=42
        )
        val_images, test_images, val_labels, test_labels = train_test_split(
            test_images, test_labels, test_size=val_ratio / (1 - train_ratio), random_state=42
        )

        # Copy files to respective directories
        for split, img_files, lbl_files in zip(splits, [train_images, val_images, test_images],
                                               [train_labels, val_labels, test_labels]):
            for img_file, lbl_file in zip(img_files, lbl_files):
                # Source paths
                img_src = os.path.join(sequence_image_dir, img_file)
                lbl_src = os.path.join(sequence_label_dir, lbl_file)

                # Destination paths
                img_dst = os.path.join(output_base_dir, 'images', split, f"{sequence}_{img_file}")
                lbl_dst = os.path.join(output_base_dir, 'labels', split, f"{sequence}_{lbl_file}")

                # Copy files
                shutil.copy2(img_src, img_dst)
                shutil.copy2(lbl_src, lbl_dst)
                print(f"Copied: {img_src} -> {img_dst}")
                print(f"Copied: {lbl_src} -> {lbl_dst}")

# Parameters
image_base_dir = '/dtu/blackhole/09/203497/Perception/final_project/dataset/training/image_02'  # Path to images
label_base_dir = '/dtu/blackhole/09/203497/Perception/final_project/dataset/training/yolo_labels'  # Path to labels
output_base_dir = '/dtu/blackhole/09/203497/Perception/final_project/splits'  # Path to save splits

split_dataset(image_base_dir, label_base_dir, output_base_dir)


Copied: /dtu/blackhole/09/203497/Perception/final_project/dataset/training/image_02/0000/000118.png -> /dtu/blackhole/09/203497/Perception/final_project/splits/images/train/0000_000118.png
Copied: /dtu/blackhole/09/203497/Perception/final_project/dataset/training/yolo_labels/0000/000118.txt -> /dtu/blackhole/09/203497/Perception/final_project/splits/labels/train/0000_000118.txt
Copied: /dtu/blackhole/09/203497/Perception/final_project/dataset/training/image_02/0000/000069.png -> /dtu/blackhole/09/203497/Perception/final_project/splits/images/train/0000_000069.png
Copied: /dtu/blackhole/09/203497/Perception/final_project/dataset/training/yolo_labels/0000/000069.txt -> /dtu/blackhole/09/203497/Perception/final_project/splits/labels/train/0000_000069.txt
Copied: /dtu/blackhole/09/203497/Perception/final_project/dataset/training/image_02/0000/000026.png -> /dtu/blackhole/09/203497/Perception/final_project/splits/images/train/0000_000026.png
Copied: /dtu/blackhole/09/203497/Perception/final